Subject: Data Visualization & Hypotheses Development Code Submission.

Date: November 28, 2024.

Dear Professor Ilia Tetin,

I am writing on behalf of our presentation team, which includes two members:

1. LE TRAN NHA TRAN - JASMINE (Student ID: 11285100M);
2. DINH VAN LONG - BRAD (Student ID: 11285109M).

Attached below, you will find the data visualizations and preliminary hypotheses we have developed.

This section provides key information along with handling on missing values and exploratory data analysis (EDA). We have also visualized the data using various graphs and charts, highlighting important metrics such as price distribution, regional differences, and trends in storage capacity and color within the used mobile phone market.

In [ ]:
%%capture
!pip install unidecode

In [ ]:
import polars as pl
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio
import unidecode

In [ ]:
USD2VND = 25418  # The exchange rate is 1 USD (US Dollars) = 25,418 VND (Vietnam Thousand Dong) as of November 23, 2024.

In [ ]:
df = pl.read_csv("info.csv")

## 1. Data Cleaning


In [ ]:
df = (
    df.with_columns(
        # Convert "list_time" column from string to date format
        pl.col("list_time").str.to_date(),
        # Replace nulls in "company_ad" with False and rename the column to "is_company"
        pl.col("company_ad").fill_null(False).alias("is_company"),
    )
    .filter(
        # Exclude rows where "mobile_brand" is "Hãng khác" (unknown or generic brand)
        (pl.col("mobile_brand") != "Hãng khác")
        # Exclude rows where "mobile_model" is "Dòng khác" (unknown or generic model)
        & (pl.col("mobile_model") != "Dòng khác")
        # Exclude rows where "mobile_capacity" is "8" (unclear value; not standard GB)
        & (pl.col("mobile_capacity") != "8")
        # Exclude rows where "price" is 60,000,000 or higher (likely outliers)
        & (pl.col("price") < 60_000_000)
    )
    .drop(
        # Drop the "full_name" column; might be redundant with "account_name"
        "full_name",
        # Drop the "company_ad" column; it's replaced by "is_company"
        "company_ad",
        # Drop the "phone" column; phone numbers are masked and not useful
        "phone",
        # Drop the "address" column; already have longitude and latitude
        "address",
        # Drop the "usage_information" column; it contains a single value (no variance)
        "usage_information",
        # Drop the "url" column; it is not useful for analysis
        "url",
    )
    .rename(
        {
            # Rename "elt_condition" to "condition" for brevity
            "elt_condition": "condition",
            # Rename "elt_origin" to "origin" for brevity
            "elt_origin": "origin",
            # Rename "elt_warranty" to "warranty" for brevity
            "elt_warranty": "warranty",
            # Rename "mobile_brand" to "brand" for brevity
            "mobile_brand": "brand",
            # Rename "mobile_capacity" to "capacity" for brevity
            "mobile_capacity": "capacity",
            # Rename "mobile_color" to "color" for brevity
            "mobile_color": "color",
            # Rename "mobile_model" to "model" for brevity
            "mobile_model": "model",
        }
    )
)

In [ ]:
df = df.with_columns(
    # Replace condition values for consistency and ease of analysis
    pl.col("condition").replace(
      {
        "Đã sử dụng (chưa sửa chữa)": "used",  # Simplify to "used"
        "Đã sử dụng (qua sửa chữa)": "refurbished",  # Distinguish repaired items
        "Mới": "new",  # Translate "Mới" to "new"
       }
    ),
    # Replace null values in "sold_ads", "total_rating", and "total_rating_for_seller" with 0
    pl.col("sold_ads").fill_null(0),
    pl.col("total_rating").fill_null(0),
    pl.col("total_rating_for_seller").fill_null(0),
    # Replace null values in ratings with -1 to indicate "no rating yet"
    pl.col("average_rating").fill_null(-1),
    pl.col("average_rating_for_seller").fill_null(-1),
    # Replace null image counts with 0
    pl.col("number_of_images").fill_null(0),
    # Replace capacity values with standardized labels
    pl.col("capacity").replace(
        {
            "< 8GB": "less_than_8", # Convert textual descriptions to standardized labels
            "8 GB": "8",
            "16 GB": "16",
            "32 GB": "32",
            "64 GB": "64",
            "128 GB": "128",
            "256 GB": "256",
            "512 GB": "512",
            "1 TB": "1024",  # Convert to GB for consistency
            "> 2 TB": "more_than_2048",  # Convert to GB and standardize
        }
    ),
    # Replace warranty values with standardized labels
    pl.col("warranty").replace(
        {
            "1 tháng": "1",  # Numeric representation for uniformity
            "2 tháng": "2",
            "3 tháng": "3",
            "4-6 tháng": "4_to_6",  # Use a range representation
            "7-12 tháng": "7_to_12",
            ">12 tháng": "more_than_12",
            "Còn bảo hành": "active",  # Indicates an active warranty
            "Bảo hành hãng": "manufacturer",  # Manufacturer warranty
            "Hết bảo hành": "expired",  # Expired warranty
        }
    ),
    # Replace null color values with "unknown" then replace color names
    # with English equivalents for consistency
    pl.col("color").fill_null("unknown").replace(
        {
            "Đỏ": "red",
            "Bạc": "silver",
            "Vàng": "gold",
            "Vàng hồng": "rose_gold",
            "Xám": "gray",
            "Xanh dương": "blue",
            "Đen": "black",
            "Đen bóng - Jet black": "black",  # Merge "Jet black" with black
            "Trắng": "white",
            "Hồng": "pink",
            "Xanh lá": "green",
            "Cam": "orange",
            "Tím": "purple",
            "Màu khác": "other",  # Generic category for uncommon colors
        }
    ),
    # Replace origin values with English equivalents for standardization
    pl.col("origin").replace(
        {
            "Đức": "germany",
            "Thái Lan": "thailand",
            "Hàn Quốc": "south_korea",
            "Đang cập nhật": "unknown",  # Placeholder for missing data
            "Việt Nam": "vietnam",
            "Mỹ": "usa",
            "Đài Loan": "taiwan",
            "Nước khác": "other",  # Generic category for uncommon origins
            "Ấn Độ": "india",
            "Nhật Bản": "japan",
            "Trung Quốc": "china",
        }
    ),
    # Replace brand names for consistent formatting
    pl.col("brand").replace(
        {
            "Q Mobile": "QMobile",  # Standardize format
            "Nokia thông minh": "Nokia_Smart",  # Distinguish between smart and feature phones
            "Nokia phổ thông": "Nokia_Feature",
        }
    ),
    # Convert prices from VND to USD and create a new column
    (pl.col("price") / USD2VND).alias("price"),
)

In [ ]:
def standardize_area_name(name):
    # Map Vietnamese area postfixes to their English equivalents
    postfix_mapping = {
        "Thành phố": "city",  # Removed "of" for brevity and consistency
        "Thị xã": "town",  # Smaller administrative division than a city
        "Quận": "district",  # Urban district
        "Huyện": "rural_district",  # Rural district
    }

    # Handle the special case of unwanted character \x08
    name = name.replace("\x08", "")

    # Split the name into parts to separate the postfix and location
    parts = name.split()

    # Determine if the postfix spans two words (e.g., "Thành phố", "Thị xã")
    postfix = " ".join(parts[:2]) if parts[0] in ["Thành", "Thị"] else parts[0]

    # Extract the location part of the name after the postfix
    location = (
        " ".join(parts[2:]) if parts[0] in ["Thành", "Thị"] else " ".join(parts[1:])
    )

    # Translate the Vietnamese postfix to its English equivalent
    new_postfix = postfix_mapping.get(postfix, postfix)

    # Transliterate the location name (remove diacritics, convert to lowercase, format with underscores)
    location = unidecode.unidecode(location)  # Remove diacritics
    location = location.lower().replace(" ", "_").replace("-", "_")

    # Combine the formatted location name with the English postfix
    return f"{location}_{new_postfix}"


def standardize_ward_name(name):
    # Map Vietnamese ward postfixes to their English equivalents
    postfix_mapping = {
        "Phường": "ward",  # Urban ward
        "Xã": "commune",  # Rural commune
        "Thị trấn": "township",  # Township
    }

    # Handle the special case of unwanted character \x08
    name = name.replace("\x08", "")

    # Split the name into parts to separate the postfix and location
    parts = name.split()

    # Handle compound postfix like "Thị trấn"
    postfix = "Thị trấn" if parts[0] == "Thị" and parts[1] == "trấn" else parts[0]

    # Extract the location part of the name after the postfix
    location = " ".join(parts[2:]) if postfix == "Thị trấn" else " ".join(parts[1:])

    # Translate the Vietnamese postfix to its English equivalent
    new_postfix = postfix_mapping.get(postfix, postfix)

    # Transliterate the location name (remove diacritics, convert to lowercase, format with underscores)
    location = unidecode.unidecode(location)
    location = location.lower().replace(" ", "_").replace("-", "_")

    # Combine the formatted location name with the English postfix
    return f"{location}_{new_postfix}"


def standardize_region_name(name):
    # Map special Vietnamese city names to their standardized English equivalents
    city_mapping = {
        "Tp Hồ Chí Minh": "ho_chi_minh_city",  # Major cities with specific English names
        "Hà Nội": "hanoi",
        "Đà Nẵng": "da_nang",
        "Hải Phòng": "hai_phong",
        "Cần Thơ": "can_tho",
    }

    # Handle compound region names with special characters
    compound_mapping = {
        "Bà Rịa - Vũng Tàu": "ba_ria_vung_tau",  # Province with hyphen
        "Thừa Thiên Huế": "thua_thien_hue",  # Region with complex name
    }

    # Check for special mappings first
    if name in city_mapping:
        return city_mapping[name]
    if name in compound_mapping:
        return compound_mapping[name]

    # For other provinces, transliterate and format the name
    location = unidecode.unidecode(name)  # Remove diacritics
    location = location.lower().replace(" ", "_").replace("-", "_")

    # Return the formatted location name
    return location

In [ ]:
df = df.with_columns(
    pl.col("region_name").map_elements(standardize_region_name, return_dtype=pl.String),
    pl.col("area_name").map_elements(standardize_area_name, return_dtype=pl.String),
    pl.col("ward_name").map_elements(standardize_ward_name, return_dtype=pl.String).fill_null("''"),
)

In [ ]:
df.head()

shape: (5, 26)
┌───────────┬───────────┬────────────┬────────────┬───┬──────────┬───────┬────────────┬────────────┐
│ ad_id     ┆ list_id   ┆ list_time  ┆ account_na ┆ … ┆ capacity ┆ color ┆ model      ┆ is_company │
│ ---       ┆ ---       ┆ ---        ┆ me         ┆   ┆ ---      ┆ ---   ┆ ---        ┆ ---        │
│ i64       ┆ i64       ┆ date       ┆ ---        ┆   ┆ str      ┆ str   ┆ str        ┆ bool       │
│           ┆           ┆            ┆ str        ┆   ┆          ┆       ┆            ┆            │
╞═══════════╪═══════════╪════════════╪════════════╪═══╪══════════╪═══════╪════════════╪════════════╡
│ 162233828 ┆ 120443732 ┆ 2024-10-24 ┆ Huỳnh      ┆ … ┆ 128      ┆ blue  ┆ 5 Pro      ┆ false      │
│           ┆           ┆            ┆ Thịnh      ┆   ┆          ┆       ┆            ┆            │
│ 162233949 ┆ 120443846 ┆ 2024-10-24 ┆ Tiến minh  ┆ … ┆ 64       ┆ black ┆ iPhone XS  ┆ false      │
│ 162233556 ┆ 120443629 ┆ 2024-10-24 ┆ Quốc Khánh ┆ … ┆ 32       ┆ black ┆ Galaxy J7  ┆ false      │
│           ┆           ┆            ┆            ┆   ┆          ┆       ┆ Prime      ┆            │
│ 162232639 ┆ 120442737 ┆ 2024-10-24 ┆ MeoBile    ┆ … ┆ 128      ┆ blue  ┆ iPhone 15  ┆ true       │
│           ┆           ┆            ┆ Điện Thoại ┆   ┆          ┆       ┆ Plus       ┆            │
│           ┆           ┆            ┆ Giá Lái    ┆   ┆          ┆       ┆            ┆            │
│ 162233960 ┆ 120443848 ┆ 2024-10-24 ┆ Di Động 86 ┆ … ┆ 256      ┆ black ┆ Redmi K70  ┆ true       │
└───────────┴───────────┴────────────┴────────────┴───┴──────────┴───────┴────────────┴────────────┘

In [ ]:
df.describe()

shape: (9, 27)
┌────────────┬────────────┬────────────┬────────────┬───┬────────────┬───────┬─────────┬───────────┐
│ statistic  ┆ ad_id      ┆ list_id    ┆ list_time  ┆ … ┆ capacity   ┆ color ┆ model   ┆ is_compan │
│ ---        ┆ ---        ┆ ---        ┆ ---        ┆   ┆ ---        ┆ ---   ┆ ---     ┆ y         │
│ str        ┆ f64        ┆ f64        ┆ str        ┆   ┆ str        ┆ str   ┆ str     ┆ ---       │
│            ┆            ┆            ┆            ┆   ┆            ┆       ┆         ┆ f64       │
╞════════════╪════════════╪════════════╪════════════╪═══╪════════════╪═══════╪═════════╪═══════════╡
│ count      ┆ 16405.0    ┆ 16405.0    ┆ 16405      ┆ … ┆ 16405      ┆ 16405 ┆ 16405   ┆ 16405.0   │
│ null_count ┆ 0.0        ┆ 0.0        ┆ 0          ┆ … ┆ 0          ┆ 0     ┆ 0       ┆ 0.0       │
│ mean       ┆ 1.6030e8   ┆ 1.1880e8   ┆ 2024-10-20 ┆ … ┆ null       ┆ null  ┆ null    ┆ 0.758244  │
│            ┆            ┆            ┆ 17:09:01.3 ┆   ┆            ┆       ┆         ┆           │
│            ┆            ┆            ┆ 71000      ┆   ┆            ┆       ┆         ┆           │
│ std        ┆ 5.5342e6   ┆ 4.6795e6   ┆ null       ┆ … ┆ null       ┆ null  ┆ null    ┆ null      │
│ min        ┆ 7.515945e7 ┆ 5.0912519e ┆ 2024-10-16 ┆ … ┆ 1024       ┆ black ┆ 1       ┆ 0.0       │
│            ┆            ┆ 7          ┆            ┆   ┆            ┆       ┆         ┆           │
│ 25%        ┆ 1.6185634e ┆ 1.20127631 ┆ 2024-10-19 ┆ … ┆ null       ┆ null  ┆ null    ┆ null      │
│            ┆ 8          ┆ e8         ┆            ┆   ┆            ┆       ┆         ┆           │
│ 50%        ┆ 1.62071792 ┆ 1.20307412 ┆ 2024-10-21 ┆ … ┆ null       ┆ null  ┆ null    ┆ null      │
│            ┆ e8         ┆ e8         ┆            ┆   ┆            ┆       ┆         ┆           │
│ 75%        ┆ 1.62161286 ┆ 1.20382772 ┆ 2024-10-23 ┆ … ┆ null       ┆ null  ┆ null    ┆ null      │
│            ┆ e8         ┆ e8         ┆            ┆   ┆            ┆       ┆         ┆           │
│ max        ┆ 1.6223423e ┆ 1.20444052 ┆ 2024-10-24 ┆ … ┆ more_than_ ┆ white ┆ v7 Plus ┆ 1.0       │
│            ┆ 8          ┆ e8         ┆            ┆   ┆ 2048       ┆       ┆         ┆           │
└────────────┴────────────┴────────────┴────────────┴───┴────────────┴───────┴─────────┴───────────┘

In [ ]:
df.write_csv("cleaned_info.csv")

Variable Descriptions:
- statistic: count, null count, mean, standard, min, max, 25%, 50%, 75%, 100%.
- ad_id: Unique identifier for each advertisement.
- list_id: Unique identifier for the listing associated with the advertisement.
- list_time: Timestamp indicating when the listing was created or updated.
- account_name: Name of the account posting the advertisement.
- price: Price of the second-hand phones' listed.
- account_id: Unique identifier for the account of the seller.
- longitude: Geographical longitude coordinate of the item location.
- latitude: Geographical latitude coordinate of the item location.
- sold_ads: Number of items sold by the seller.
- total_rating: Total number of ratings received by the seller.
- total_rating_for_seller: Ratings specifically received as a seller, from customers.
- average_rating: Average rating across all interactions for the account.
- average_rating_for_seller: Average rating received specifically for selling activities.
- account_oid: Unique identifier (alternative or additional ID) for the account.
- area_name: Specific name of the area where the consumption is located (Vietnam's Districts).
- region_name: Specific name of the region where the consumption is listed (Vietnam's Provinces).
- number_of_images: Number of images included in the listing.
- ward_name: Specific name of the ward associated with the item's location (Vietnam's Wards or Communes).
- condition: The condition of the item being sold (e.g., new, used, other).
- origin: Origin of the item (e.g., country of manufacture or brand origin).
- warranty: Information about the item's warranty (e.g., active, expired, manufacturer, etc).
- brand: The brand of the item (e.g., Apple, Samsung, Huawei, etc).
- capacity: Item's capacity specification (e.g., memory size, storage).
- color: Color of the item (e.g., black, white, gold, etc).
- model: Model name or identifier of the item (e.g., Plus, Max, Pro Max, Note, etc).
- is_company: Boolean flag indicating whether the seller is a company (TRUE) or an individual (FALSE).

## 2. EDA


In [ ]:
cleaned_info = pd.read_csv('cleaned_info.csv') # Load the data into the 'info' DataFrame

# Check for missing values
missing_values = cleaned_info.isnull().sum() # Changed 'cleaned_info_df' to 'cleaned_info'
print("Missing values per column:")
print(missing_values)

Missing values per column:
ad_id                        0
list_id                      0
list_time                    0
account_name                 0
price                        0
account_id                   0
longitude                    0
latitude                     0
sold_ads                     0
total_rating                 0
total_rating_for_seller      0
average_rating               0
average_rating_for_seller    0
account_oid                  0
area_name                    0
region_name                  0
number_of_images             0
ward_name                    0
condition                    0
origin                       0
warranty                     0
brand                        0
capacity                     0
color                        0
model                        0
is_company                   0
dtype: int64


In [ ]:
# Find the largest price in the 'price' column
largest_price = cleaned_info['price'].max()
largest_price
print("Largest price:", "$USD", largest_price, )

Largest price: $USD 2045.794318986545


In [ ]:
# Find the minimum price in the 'price' column
minimum_price = cleaned_info['price'].min()
minimum_price
print("Minimum price:", "$USD", minimum_price)

Minimum price: $USD 0.3934219844204894


In [ ]:
# Find the largest value in the 'sold_ads' column
largest_sold_ads = cleaned_info['sold_ads'].max()
largest_sold_ads
print("Larges ads sold:", largest_sold_ads)

Larges ads sold: 7000


In [ ]:
# Calculate total people bought in the region "ho_chi_minh_city"
total_buyers_ho_chi_minh_city = cleaned_info[cleaned_info['region_name'] == 'ho_chi_minh_city'].shape[0]
total_buyers_ho_chi_minh_city
print("The total number of buyers in Ho Chi Minh:", total_buyers_ho_chi_minh_city)

The total number of buyers in Ho Chi Minh: 7323


In [ ]:
# Calculate the total number of buyers who bought the brand "Apple"
total_buyers_apple = cleaned_info[cleaned_info['brand'] == 'Apple'].shape[0]
total_buyers_apple
print("The total number of buyers who purchased Apple brand:",total_buyers_apple)

The total number of buyers who purchased Apple brand: 8021


In [ ]:
# Calculate the total number of buyers who bought the brand "Samsung""
total_buyers_samsung = cleaned_info[cleaned_info['brand'] == 'Samsung'].shape[0]
total_buyers_samsung
print("The total number of buyers who purchased Samsung brand:",total_buyers_samsung)

The total number of buyers who purchased Samsung brand: 3859


In [ ]:
# Calculate total company sellers (where 'is_company' = 'TRUE')
# Use 'TRUE' (string) instead of TRUE (variable) for comparison
total_company_sellers = cleaned_info[cleaned_info['is_company'] == True].shape[0]

print("The total number of company sellers:", total_company_sellers)

The total number of company sellers: 12439


In [ ]:
# Calculate total individual sellers (where 'is_company' = 'FALSE')
# Use 'FALSE' (string) instead of FALSE (variable) for comparison
total_individual_sellers = cleaned_info[cleaned_info['is_company'] == False].shape[0]

print("The total number of individual sellers:", total_individual_sellers)

The total number of individual sellers: 3966


In [ ]:
# Calculate the total number of items sold with 'origin' = 'Việt Nam' (Vietnam)
total_items_sold_vietnam = cleaned_info[cleaned_info['origin'].str.lower() == 'vietnam'].shape[0]

print("Total items sold with origin as Vietnam:", total_items_sold_vietnam)

Total items sold with origin as Vietnam: 4311


In [ ]:
# Set the default template to "plotly_white" for all figures
# This ensures a clean and minimalistic white background for plots
pio.templates.default = "plotly_white"

# Configuration for better display in notebook
config = {
    "displayModeBar": True,  # Show the toolbar (mode bar) for interaction
    "scrollZoom": True,  # Enable zooming with the mouse scroll wheel
    "displaylogo": False,  # Remove the Plotly logo from the toolbar
    # Remove unnecessary mode bar buttons for 2D selections
    "modeBarButtonsToRemove": ["lasso2d", "select2d"],
}

# Define common layout settings for all figures
layout = dict(
    font=dict(size=12),  # Set a consistent font size for text in the plot
    showlegend=True,  # Enable legends by default
)

# Define common figure dimensions for all plots
fig_width = 900  # Set the width of the figure in pixels
fig_height = 500  # Set the height of the figure in pixels

### 2.1 Price Analysis


#### 2.1.1 Distribution of prices across brands


In [ ]:
# Create a box plot to visualize the price distribution for each brand
fig = px.box(
    df.to_pandas(),  # Convert the dataframe to pandas for compatibility with Plotly
    x="brand",  # Brands on the x-axis
    y="price",  # Prices on the y-axis
    title="Price Distribution by Brand",  # Set plot title
    height=fig_height,  # Use predefined figure height
    width=fig_width,  # Use predefined figure width
)

# Update layout settings for better visualization
fig.update_layout(
    **layout,  # Apply common layout settings (e.g., font size, legend display)
    xaxis_tickangle=45,  # Angle brand names on x-axis for better readability
    yaxis_title="Price (USD)",  # Set label for y-axis
    margin=dict(l=0, r=0, t=30, b=100),  # Adjust margins to accommodate rotated labels
)

# Display the box plot with the predefined configuration
fig.show(config=config)

(1) Price Distribution by Brand Chart:
- Apple dominates the high-end price range, with significant variability in price (wide box and whisker plot). This suggests that Apple products hold value across various conditions and models, likely due to their strong brand reputation and consumer trust.
- Brands like Samsung, Xiaomi, and Realme are clustered in the mid-price range, with smaller variability. These brands are appealing to value-conscious buyers, where price may be a primary decision factor.
- Lesser-known brands like Realme, Oppo, and Vsmart have a narrower price range, likely targeting budget-conscious consumers with minimal price variability.
- Other brands: Brands like Sony, Honor, and Vertu show significantly higher price variability, with some outliers exceeding $1500, indicating the presence of high-end models.

*Price outliers.* Several brands (Apple, Samsung, BlackBerry, etc) have significant price outliers, suggesting that while most devices are priced within a reasonable range, a few premium or rare models inflate the maximum values.

In [ ]:
# Compute top models per brand by grouping and aggregating
top_models = (
    df.group_by(["brand", "model"])  # Group data by brand and model
    .agg(
        avg_price=pl.col("price").mean(),  # Calculate the average price for each model
        count=pl.col("price").count(),  # Count the number of entries for each model
    )
    .sort(["brand", "count"], descending=True)  # Sort by brand and model count
    .group_by("brand")  # Group again by brand
    .head(5)  # Take top 5 models per brand based on count
    .sort("avg_price", descending=True)  # Sort final output by average price
)

# Create a bar plot to display average prices for top models per brand
fig = px.bar(
    top_models.to_pandas(),  # Convert to pandas for compatibility with Plotly
    x="model",  # Models on the x-axis
    y="avg_price",  # Average prices on the y-axis
    color="brand",  # Differentiate by brand with color
    title="Average Price by Top Models per Brand",  # Set plot title
    height=fig_height,  # Use predefined figure height
    width=fig_width,  # Use predefined figure width
)

# Update layout for better visualization
fig.update_layout(
    **layout,  # Apply common layout settings
    xaxis_tickangle=45,  # Angle model names for readability
    yaxis_title="Average Price (USD)",  # Label the y-axis
    margin=dict(l=0, r=0, t=30, b=100),  # Adjust bottom margin for rotated labels
    legend=dict(
        yanchor="top",  # Anchor the legend at the top
        y=0.99,  # Position legend near the top
        xanchor="right",  # Anchor the legend on the right
        x=0.99,  # Position legend near the right edge
        bgcolor="rgba(255, 255, 255, 0.8)",  # Add semi-transparent white background
        bordercolor="rgba(0, 0, 0, 0.2)",  # Add a subtle border color
        borderwidth=1,  # Set border width
    ),
)

# Display the bar plot with the predefined configuration
fig.show(config=config)

(2) Average Price by Top Models per Brand Chart:

- Price disparities by "Brand" and "Model":

There is a significant variance in average prices across different brands, especially for the latest versions of flagship models. These models often act as outliers, driving up the average price for specific brands. In contrast, models that have been on the market for a while tend to exhibit a more stable and predictable price range, suggesting depreciation or consistent market valuation over time.
- Premium vs. Budget Brands:

Some brands (e.g., Apple, Samsung, and Vertu) exhibit notably higher average prices compared to others, reflecting their positioning in the premium segment. Meanwhile, brands like Xiaomi and Realme maintain a lower price range, appealing to budget-conscious consumers. Some emerging competitors like OnePlus, Google, and Asus are leaning toward premium and niche pricing, possibly targeting tech-savvy users.
- Brand Diversification:

Brands such as Samsung and OnePlus span a broad price range. For instance, models like the Samsung Galaxy S21 Ultra appear in the premium segment, while other models cater to mid-range users.

Overall, certain brands display a wider spread between their models' prices *(as the graph showcases a representative selection of 5 models per brand)*, indicating a diverse product lineup catering to different market segments (from entry-level to flagship).

As a result:

- Price sensitivity: Brands in the mid-range price category (e.g., Samsung, Xiaomi) may see a more direct influence from comments and ratings. For instance, if a product offers better-than-expected performance, reviews will emphasize "value for money" which can significantly boost sales.

- Impact of review: Negative reviews or comments about durability, condition, or after-sales support could disproportionately impact lower-priced brands or refurbished models, as these buyers are more sensitive to perceived risks.

#### 2.1.2 Average price by condition


In [ ]:
condition_summary = (
    df.group_by("condition")  # Group the data by the "condition" column
    .agg(
        [
            # Calculate the mean price for each condition group
            pl.col("price").mean().alias("avg_price"),
            # Calculate the standard deviation of prices for each condition group
            pl.col("price").std().alias("std_price"),
            # Count the number of records for each condition group
            pl.col("price").count().alias("count"),
        ]
    )
    # Sort the resulting summary by average price in descending order
    .sort("avg_price", descending=True)
)

fig = go.Figure()  # Initialize a new Plotly figure

# Add a bar chart to the figure
fig.add_bar(
    x=condition_summary["condition"],  # X-axis: different conditions (categories)
    y=condition_summary["avg_price"],  # Y-axis: average price for each condition
    error_y=dict(
        type="data",  # Use data for the error values
        array=condition_summary["std_price"],  # Set error bars as the standard deviation
        visible=True,  # Display the error bars
    ),
)

fig.update_layout(
    title="Average Price by Condition",
    xaxis_title="Condition",
    yaxis_title="Average Price (USD)",
    **layout,
    width=fig_width,
    height=fig_height,
)
fig.show(config=config)

The bar chart displays the average price of smartphones based on their condition (new, used, or refurbished).

- New phones have the highest average price, with a wider variability (large error bars), reflecting a mix of entry-level and high-end models, likely driven by differences in brands and models.

- Used phones have a moderate average price, lower than new phones (~$273.77 ± $244.41), reflecting their depreciation due to prior usage. The variability is slightly lower compared to new phones, suggesting a narrower price range. This indicates that buyers of used phones may have a more standardized expectation for pricing.

- Refurbished phones have the lowest average price among the three conditions, possibly because buyers may still perceive them as risky despite repairs and certifications. The error bars indicate moderate variability, suggesting a balance between perceived value and pricing consistency.

In this scenario:
  - The close average prices and overlapping ranges for used and refurbished devices suggest that buyers may perceive them similarly in value or that refurbished devices vary significantly in quality.

  - Refurbished phones might require stronger trust-building efforts, such as reviews and detailed comments, to assure buyers of their quality and value. New phones, though commanding higher prices, might rely less on reviews but could benefit from testimonials confirming their condition and performance.

Consumers' Insights:
- Buyers of used and refurbished phones are likely more price-sensitive and heavily influenced by perceived value through consumer feedback.

- Competitive pricing, combined with positive ratings, could significantly impact sales in these categories.

#### 2.1.3 Price trends by region


In [ ]:
region_summary = (
    df.group_by("region_name")  # Group data by the Vietnam's region name
    .agg(
        [
            # Calculate the mean price for each region
            pl.col("price").mean().alias("avg_price"),
            # Count the number of listings in each region
            pl.col("price").count().alias("count"),
        ]
    )
    .sort("avg_price", descending=True)  # Sort by average price in descending order
)

# Create two subplots
fig = make_subplots(
    rows=1,  # One row of plots
    cols=2,  # Two columns (one for each plot)
    subplot_titles=("Average Price by Vietnam's Region", "Listing Count by Vietnam's Region"),  # Titles
)

fig.add_trace(
    go.Bar(
        x=region_summary["region_name"],  # Regions on the x-axis
        y=region_summary["avg_price"],  # Average price on the y-axis
        name="Average Price",  # Legend entry
    ),
    row=1,  # First row
    col=1,  # First column
)

region_summary = region_summary.sort("count", descending=True)  # Sort by count

fig.add_trace(
    go.Bar(
        x=region_summary["region_name"],  # Regions on the x-axis
        y=region_summary["count"],  # Listing count on the y-axis
        name="Count",  # Legend entry
    ),
    row=1,  # First row
    col=2,  # Second column
)

fig.update_layout(
    height=fig_height,
    width=fig_width * 1.5,  # wider for two plots
    **layout,
)
fig.update_xaxes(tickangle=45)
fig.show(config=config)

1. Average Price by Vietnam's Region (Left Chart):

- Urban areas (e.g., Ho Chi Minh City, Hanoi Capital): These cities dominate both the listing count and average price, indicating a larger and more competitive market.
Sellers in urban areas likely list more premium models and newer phones, driving up the average price.

Buyers in these regions tend to be brand-conscious and quality-driven due to its wealthier customer base, who are willing to pay a premium, influenced by factors such as brand reputation and product condition.

The market in these areas also experiences higher competition among sellers. Price variations in similar models can likely be attributed to perceived value, influenced by ratings, reviews, and product condition descriptions.

- Rural or smaller provinces (e.g., Gia Lai, Binh Thuan): Fewer listings and lower average prices reflect a smaller market, likely driven by affordability and demand for used or refurbished phones.
Buyers focus more on price sensitivity and affordability due to limited purchasing power.

Sellers in these regions may struggle to list higher-priced models due to limited buyer purchasing power.

2. Listing Count by Vietnam's Region (Right Chart):

Ho Chi Minh City dominates with the highest number of listings, followed by Hanoi and Binh Duong. These regions are major economic hubs with a high density of sellers.

Rural areas with fewer listings may see buyers leveraging their bargaining power for lower prices, given the limited supply and perceived risk of second-hand products.

Overall, the skewed distribution of listings suggests that the variation in average prices aligns with regional economic development and consumer purchasing power, with urban areas outpacing rural ones.

3. Market Trends:

- The significant concentration of listings in a few key regions suggests that most sellers prefer to operate in densely populated areas where demand is high.
- This leaves opportunities for digital platforms to better serve underrepresented areas through localized marketing or logistics solutions.

#### 2.1.4 Price vs capacity correlation


In [ ]:
# Get top N brands by count to reduce clutter
top_brands = (
    df.group_by("brand")  # Group by brand
    .len()  # Count the number of listings for each brand
    .sort("len", descending=True)  # Sort by count in descending order
    .head(10)  # Select the top 10 brands
    .get_column("brand")  # Extract the brand names as a column
)

# Define capacity groups for categorization
capacities_groups = [
    ["less_than_8", "8", "16", "32"],  # Low capacity
    ["64", "128"],  # Medium capacity
    ["256", "512", "1024", "more_than_2048"],  # High capacity
]

fig = make_subplots(
    rows=3,  # Three rows for each capacity group
    cols=1,  # Single column
    subplot_titles=("Low Capacity", "Medium Capacity", "High Capacity"),  # Titles
)

# Iterate through each capacity group and its corresponding row index
for idx, cap_group in enumerate(capacities_groups, 1):
    # Filter data for the current capacity group and top brands
    plot_data = df.filter(
        (pl.col("brand").is_in(top_brands)) & (pl.col("capacity").is_in(cap_group))
    )

    # Create a box plot using Plotly Express
    box_fig = px.box(
        plot_data.to_pandas(),  # Convert to pandas for compatibility
        x="capacity",  # X-axis: capacities within the current group
        y="price",  # Y-axis: price
        color="brand",  # Differentiate by brand using colors
        category_orders={"capacity": cap_group},  # Ensure capacity order matches the group
    )

    # Add each trace (box plot) to the subplot
    for trace in box_fig.data:
        fig.add_trace(trace, row=idx, col=1)

fig.update_layout(
    height=fig_height * 2,  # Double the height for better spacing
    width=fig_width,  # Maintain the predefined width
    boxmode="group",  # Group boxes by brand within each capacity
    showlegend=True,  # Show the legend
    legend=dict(
        yanchor="top",  # Anchor the legend to the top
        y=0.99,  # Position it near the top of the figure
        xanchor="right",  # Anchor the legend to the right
        x=0.99,  # Position it near the right edge
        bgcolor="rgba(255, 255, 255, 0.8)",  # Semi-transparent white background
        bordercolor="rgba(0, 0, 0, 0.2)",  # Subtle border color
        borderwidth=1,
    ),
    margin=dict(l=0, r=0, t=50, b=50),  # Adjust margins for spacing
)

fig.update_yaxes(title_text="Price (USD)", tickformat=",")
fig.show(config=config)

*Market position:*

Brands like Apple are less represented in this category, as most of their devices start at higher capacities, aligning with their premium brand positioning.

(1) Low Capacity (less than 32GB): Huawei and Samsung seem to have a higher price range for these capacities, likely due to model-specific demand or premium features despite the low capacity, suggesting these models target entry-level or budget-conscious buyers.

(2) Medium Capacity (64GB and 128GB): This category shows a diverse price range across brands, reflecting that 128GB storage is a standard offering in mid-range to flagship devices.

Apple shows significantly higher prices in this range, compared to Samsung, Oppo, and Vivo, which dominate the lower-mid pricing. It's likely catering to a wide consumer demographic from budget-conscious buyers to mid-tier users.
- Medium capacities are the most diverse in terms of pricing and brand representation (prices are spread widely from $300  to  $1,500).

(3)High Capacity (256GB, 512GB, 1024GB): Apple dominates, followed by Samsung. Huawei and Samsung compete in the higher-capacity market but at lower price points compared to Apple, suggesting they target more price-sensitive users seeking larger storage.

*About pricing spread:*
- High-capacity devices (256GB, 512GB, 1TB) command premium prices, with a few exceeding $2,000.
- There is greater variability in this category, with outliers indicating a few ultra-premium models or devices in limited demand.
- Models exceeding 1TB or "more than 2048GB" are rare, and their prices reflect a niche market for power users or professionals.




A clear trend is observed: higher storage capacities correspond to higher prices, with premium brands commanding larger price margins.

### 2.2 Seller Analysis


#### 2.2.1 Distribution of seller ratings


In [ ]:
# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add histogram of ratings
fig.add_trace(
    go.Histogram(
        x=df.filter(pl.col("average_rating") >= 0)["average_rating"],  # Filter for valid ratings (>= 0)
        name="Rating Distribution",  # Legend entry name
        nbinsx=20,  # Number of bins for the histogram
    ),
    secondary_y=False,  # Assign to the primary y-axis
)

# Add cumulative distribution
fig.add_trace(
    go.Histogram(
        x=df.filter(pl.col("average_rating") >= 0)["average_rating"],  # Same filtered ratings
        name="Cumulative",  # Legend entry name
        cumulative_enabled=True,  # Enable cumulative histogram
        nbinsx=20,  # Use the same number of bins for consistency
    ),
    secondary_y=True,  # Assign to the secondary y-axis
)

fig.update_layout(
    title="Rating Distribution and Cumulative Distribution",
    xaxis_title="Average Rating",
    yaxis_title="Frequency",  # Label for primary y-axis
    yaxis2_title="Cumulative Count",  # Label for secondary y-axis
    **layout,  # Apply common layout settings
    height=fig_height,  # Set figure height
    width=fig_width,  # Set figure width
    legend=dict(
        yanchor="top",
        y=0.99,
        xanchor="right",
        x=0.99,
        bgcolor="rgba(255, 255, 255, 0.8)",  # Semi-transparent legend background
        bordercolor="rgba(0, 0, 0, 0.2)",
        borderwidth=1,
    ),
)
fig.show(config=config)

From Rating Distribution and Cumulative Distribution Chart:

 (1) Rating concentration (blue bar):

- The majority of seller ratings are in the 4–5 range *(the cumulative curve steeply rises after the 4-star mark)*, indicating that most sellers on Chotot.com maintain high ratings, suggesting that most consumers are either satisfied or very satisfied with their experiences on the platform or reliable service and perceived product quality.

- There are fewer sellers with ratings below 3, and ratings of 1 are particularly rare. This reflects a positive perception of sellers overall, yet negative experiences are less frequent but still present.

(2) Cumulative count (red bar): As shown in the graph, the cumulative distribution rises steeply at higher ratings, showing that a large proportion of sellers consistently achieve positive feedback from buyers (with over 80% of total ratings being 4 stars or above). Reaching 5-star ratings accounts for the final accumulation, meaning it represents the uppermost tier of seller satisfaction.

*Consumer Purchasing Behavior:*

- Trust in Sellers:
    - High ratings (4–5) significantly boost buyer trust, making these sellers more competitive and likely to secure faster sales.
    - Buyers are likely to prioritize listings from sellers with high ratings over those with average or low ratings.
- Low-rated Sellers:
  - Sellers with ratings below 3 might face challenges attracting buyers, as poor ratings often correlate with negative buyer experiences (e.g., misrepresented products, delayed shipping).


#### 2.2.2 Relationship between company ad and prices:


In [ ]:
# Box plot comparing prices between company and non-company ads
fig = go.Figure()

# Box plots for company and non-company ads
for is_company in [True, False]:  # Iterate over the two groups (company and individual)
    fig.add_trace(
        go.Box(
            y=df.filter(pl.col("is_company") == is_company)["price"],  # Filter prices by group
            name="Company" if is_company else "Individual",  # Set group label
            boxpoints="outliers",  # Display outliers as individual points
        )
    )

fig.update_layout(
    title="Price Distribution: Company vs Individual Sellers",  # Chart title
    yaxis_title="Price (USD)",  # Y-axis label
    **layout,  # Common layout settings
    width=fig_width,  # Predefined width
    height=fig_height,  # Predefined height
)

fig.show(config=config)


The boxplot compares the price distribution of smartphones sold by companies versus individual sellers.

- Company sellers (Blue boxplot):

    - The interquartile range (IQR) for company sellers is relatively narrow, with a minimum price: $0.46 USD and a higher median price, indicating more consistent pricing compared to individual sellers.
    - Interquartile Range (IQR): Spans from  109.76USD(Q1)to 408.96 USD (Q3) - a narrower IQR, indicating more consistent pricing.

    - Outliers: Extend up to $1,475.33 USD, indicating premium products. Overall, there are fewer extreme outliers for company sellers, reinforcing the idea of controlled and standardized pricing on Chotot.com.

- Individual Sellers (Red boxplot), with a median price:  157.37USD and minium price: 0.39USD.

  - The prices are more concentrated around the lower end, with the IQR extending further than company sellers. This indicates that individual sellers on Chotot.com are more likely to list budget-friendly or used items.
  - Interquartile Range (IQR):  66.88USD(Q1)to 346.21 USD (Q3), a wider IQR, suggesting greater variability in prices. This could result from diverse product conditions, usage durations, or personal pricing strategies.

  - Outliers: Extend up to $1,510.74 USD, with numerous outliers, suggesting occasional listings with unusually high or low prices, possibly reflecting premium models, bundles, or rare items.

Outliers:
- Both categories have some high-price outliers, but companies show fewer high-priced listings, while individual sellers’ outliers may represent a rarer listings.
- However, while companies appear to offer high-priced items, individuals also list a notable number of high-end or exclusive devices, as indicated by their outliers.

#### 2.2.3 Number of listings per seller


In [ ]:
# Get top 20 sellers by listing count
top_sellers = (
    df.group_by("account_id")  # Group data by seller's account ID
    .agg(
        pl.len().alias("listing_count"),  # Count the number of listings per seller
        pl.col("account_name").first().alias("name"),  # Get the seller's name
        pl.col("average_rating").first().alias("rating"),  # Get the seller's average rating
    )
    .sort("listing_count", descending=True)  # Sort sellers by listing count in descending order
    .head(20)  # Select the top 20 sellers
)

# Create bar chart
fig = go.Figure()

fig.add_trace(
    go.Bar(
        x=top_sellers["name"],  # Seller names on the x-axis
        y=top_sellers["listing_count"],  # Number of listings on the y-axis
        text=top_sellers["listing_count"],  # Display listing count as text on bars
        textposition="auto",  # Automatically position text on bars
    )
)

fig.update_layout(
    title="Top 20 Sellers by Number of Listings",  # Chart title
    xaxis_title="Seller Name",  # Label for x-axis
    yaxis_title="Number of Listings",  # Label for y-axis
    xaxis_tickangle=45,  # Rotate x-axis labels for better readability
    **layout,  # Apply common layout settings
    width=fig_width,  # Predefined chart width
    height=fig_height,  # Predefined chart height
)

fig.show(config=config)

The bar chart displays the top 20 sellers by the number of listings for Chotot.com's used smartphones.

- Some top sellers have significantly higher activity compared to the rest (ranging from 130 to 150 listings).

- The gap between sellers ranked 3rd to 20th is relatively narrow, ranging between 46 and 97 listings. This gradual decrease in the number of listings after the top few sellers indicates a moderately competitive environment for sellers in this segment.

As shown in the graph, unlike major corporations, the market for used phones on Chotot.com appears to be heavily driven by individual sellers and small-to-medium enterprises (SMEs). These sellers are potentially more agile in meeting the needs of price-sensitive consumers looking to sell old devices and purchase newer, better ones, highlighting the decentralized nature of this marketplace.

### 2.3 Brand/Model Analysis


#### 2.3.1 Market Share by Brand


In [ ]:
# Calculate market share percentages
brand_share = (
    df.group_by("brand")  # Group the data by brand
    .agg(pl.len().alias("count"))  # Count the number of listings for each brand
    .with_columns(
        (pl.col("count") / pl.col("count").sum() * 100).alias("percentage")  # Calculate percentage
    )
    .sort("percentage", descending=True)  # Sort brands by market share in descending order
)

# Create pie chart
fig = px.pie(
    brand_share,  # DataFrame containing the market share data
    values="percentage",  # Values for the pie slices
    names="brand",  # Labels for the pie slices
    title="Market Share by Brand",  # Title of the pie chart
    width=fig_width,  # Predefined figure width
    height=fig_height,  # Predefined figure height
)
fig.update_traces(
    textposition="inside",  # Display text inside the pie slices
    textinfo="percent+label",  # Show both percentage and label
)

fig.update_layout(layout)
fig.show(config=config)

The pie chart illustrates the market share of used smartphone brands based on the proportion of listings.

1. Dominance of Apple: Apple holds the largest market share at 52.3%, indicating a strong consumer preference for its products, even in the second-hand market. This dominance suggests Apple’s consistent brand reputation, high perceived value, and strong resale demand.
2. Samsung as the Runner-up: Samsung accounts for 21% of the market share, making it the second-largest player. Samsung's wide product range, from budget to premium models, likely contributes to its strong position.
3. Mid-Tier Brands: Xiaomi holds 9.79%, reflecting its appeal as a budget-friendly option with competitive features. Oppo contributes 6.5%, indicating its appeal among cost-conscious buyers, particularly in markets where affordability is a key factor.
4. Fragmented Minor Shares: Collectively, Vivo, Realme and Huawei brands cater to budget-conscious buyers who prioritize affordability over brand prestige. Sony and LG hold smaller portions of the market but remain relevant for buyers looking for specific features (e.g., Sony’s camera technology or LG’s unique form factors). This fragmentation indicates that consumers have diverse options, but these brands face challenges in achieving the same brand loyalty as Apple and Samsung.

#### 2.3.2 Most Common Models (top 20)


In [ ]:
# Count listings by brand and model
model_counts = (
    df.group_by(["brand", "model"])  # Group by both brand and model
    .agg(pl.len().alias("count"))  # Count the number of listings for each combination
    .sort("count", descending=True)  # Sort by count in descending order
    .head(20)  # Select the top 20 models with the highest counts
)

fig = px.bar(
    model_counts,  # DataFrame containing the top models
    x="count",  # Count of listings on the x-axis
    y="model",  # Phone models on the y-axis
    color="brand",  # Differentiate models by brand using colors
    title="Most Common Phone Models",  # Title of the bar chart
    width=fig_width,  # Predefined chart width
    height=fig_height,  # Predefined chart height
    orientation="h",  # Use horizontal bars for better readability
)

fig.update_layout(
    showlegend=True,  # Display the legend
    legend=dict(
        yanchor="top",  # Anchor the legend at the top
        y=0.99,  # Position the legend near the top
        xanchor="right",  # Anchor the legend on the right
        x=0.99,  # Position the legend near the right edge
    ),
    margin=dict(l=0, r=0, t=30, b=0),  # Adjust margins for better spacing
)

fig.update_layout(
    yaxis={"categoryorder": "total ascending"},  # Order models by count (ascending)
    xaxis_title="Count",  # Label for the x-axis
    yaxis_title="Model",  # Label for the y-axis
)
fig.show(config=config)

The bar chart shows the most common phone models listed.

The chart shows Apple models dominating the listings, with popular models like: The iPhone 12 Pro Max is the most common model, followed by iPhone 14 Pro Max and iPhone 11 Pro Max. Other flagship models like iPhone 11 Pro Max, iPhone XS Max, and newer models such as iPhone 15 Pro Max also have significant counts.

Among the predominantly Apple-dominated list, Samsung Galaxy S22 Ultra nd Galaxy Note 20 Ultra appear as the most notable Android competitor.

While the chart heavily favors Apple and Samsung, brands like Xiaomi, Oppo, and Vivo are gaining ground in Vietnam, particularly in the mid-range and budget segments, due to their competitive pricing.

Most of the common models (e.g., Pro Max, Pro, Plus versions) represent premium variants of iPhones, suggesting that buyers favor devices with better features and specifications. Notably, the overwhelming presence of Apple models reflects their strong brand loyalty, high resale value, and continued demand in the second-hand market.

Through Chotot.com, we can see that Vietnam’s second-hand smartphone market is robust, driven by:

- Price-conscious buyers seeking premium devices at lower prices.

- A culture of frequent upgrades, where consumers resell older models to fund new purchases.

#### 2.3.3 Storage Capacity Preferences


In [ ]:
capacity_dist = (
    df.group_by("capacity")  # Group data by the "capacity" column
    .agg(pl.len().alias("count"))  # Count the number of listings for each capacity
    .sort("count", descending=True)  # Sort capacities by count in descending order
)

fig = px.bar(
    capacity_dist,  # DataFrame containing the capacity distribution
    x="capacity",  # Storage capacities on the x-axis
    y="count",  # Number of listings on the y-axis
    title="Distribution of Storage Capacities",  # Chart title
    width=fig_width,  # Predefined chart width
    height=fig_height,  # Predefined chart height
)

fig.update_layout(layout)
fig.show(config=config)


The bar chart illustrates the distribution of smartphone storage capacities.

Based on the chart, we can see that the 128GB storage capacity has the highest count with 701 listings, significantly outpacing other capacities. This reflects consumer preference for a "sweet spot" balance between affordability and functionality. It is likely a "sweet spot" for most buyers in Vietnam, offering enough storage for photos, apps, and videos without the premium cost of higher capacities.

- 256GB is the second-most common storage capacity, with nearly half the listings compared to 128GB.

- 64GB still holds a significant share, indicating demand among price-sensitive buyers or those who rely on cloud storage solutions.

- 32GB, 16GB, and 8GB have a much smaller presence, reflecting their decline in popularity as these capacities struggle to meet modern app and media requirements.

Finally, capacities like 512GB and 1TB represent a niche segment.

*Future market trends:* As apps and multimedia content continue to grow in size, demand for higher capacities like 512GB and beyond is likely to increase. Hence, sellers may need to phase out lower-capacity devices to stay relevant.


#### 2.3.4 Popular Color Choices by Brand


In [ ]:
color_brand_long = (
    df.group_by(["brand", "color"])  # Group data by brand and color
    .agg(pl.len().alias("count"))  # Count the number of listings for each combination
    .sort("count", descending=True)  # Sort by count in descending order
)

# Define color mapping that matches the actual colors
color_mapping = {
    "black": "#000000",  # Black color
    "gold": "#FFD700",  # Gold color
    "white": "#FFFFFF",  # White color
    "blue": "#0000FF",  # Blue color
    "other": "#808080",  # Gray for "other"
    "purple": "#800080",  # Purple color
    "green": "#008000",  # Green color
    "silver": "#C0C0C0",  # Silver color
    "rose_gold": "#B76E79",  # Rose gold color
    "gray": "#808080",  # Gray color
    "pink": "#FFC0CB",  # Pink color
    "red": "#FF0000",  # Red color
    "orange": "#FFA500",  # Orange color
}

fig = px.bar(
    color_brand_long,  # Data containing brand, color, and count
    x="brand",  # Brands on the x-axis
    y="count",  # Number of listings on the y-axis
    color="color",  # Differentiate bars by color
    title="Color Distribution by Brand",  # Chart title
    width=fig_width,  # Predefined chart width
    height=fig_height,  # Predefined chart height
    color_discrete_map=color_mapping,  # Use custom color mapping
)

# Improve layout
fig.update_layout(
    layout,  # Apply consistent layout settings
    xaxis_title="Brand",  # Label for x-axis
    yaxis_title="Count",  # Label for y-axis
    legend=dict(
        title="Phone Color",  # Title for the legend
        yanchor="top",  # Anchor the legend at the top
        y=0.99,  # Position the legend near the top of the chart
        xanchor="right",  # Anchor the legend to the right
        x=0.99,  # Position the legend near the right edge
    ),
    bargap=0.2,  # Set gap between bars for better readability
)

# Rotate x-axis labels for better readability
fig.update_xaxes(tickangle=45)

fig.show(config=config)

The bar chart illustrates the color distribution of smartphones across different brands in Chotot.com used smartphone market.

- The most common colors for Apple include: Black, Gold, and Silver, which are traditionally popular and versatile. Rose Gold and White also appear prominently, reflecting Apple’s influence on color trends.
- Samsung has the second-highest count of listings, with Black and Gold being the most frequent colors. Additional colors like Blue, Gray, and Green reflect Samsung's strategy to appeal to younger, trend-conscious buyers, indicating a slightly more diversity in color options.
- Brands like Xiaomi, Oppo, and Huawei show smaller distributions, with a focus on basic colors like Black, White, and Gold.
- Emerging brands (e.g., Vsmart, Realme) and niche players (e.g., LG, Nokia) have minimal representation across color options, indicating a focus on affordability over aesthetic diversity.

### 2.4 Geographic Analysis


####2.4.1  Geographic distribution of sellers

In [ ]:
fig = px.scatter_mapbox(
    df,  # The dataframe containing the data
    lat="latitude",  # Latitude column for map plotting
    lon="longitude",  # Longitude column for map plotting
    color="is_company",  # Differentiate points by whether it's a company listing
    size="price",  # Size of the points corresponds to the listing price
    hover_data=["account_name", "price", "brand", "model"],  # Data to display on hover
    zoom=5,  # Initial zoom level
    title="Geographic Distribution of Sellers",  # Title of the map
)

fig.update_layout(
    mapbox_style="carto-positron",  # Use a light, clean map style
    **layout,  # Apply common layout settings
    width=fig_width,  # Set figure width
    height=fig_height,  # Set figure height
)
fig.show(config=config)

The map shows the geographic distribution of sellers for used mobile phones on a platform, with sellers categorized as either individuals or companies:

Company Presence:
- Companies (red dots), representing companies, are more prominent in highly commercial and densely populated regions, likely due to higher commercial activity and better market infrastructure.
- Example: A company, NHAT VY MOBILESTORE, selling an iPhone 11 Pro Max for approximately 39 million VND, is located at latitude 11.95256 and longitude 108.4267

Individual Sellers:
- Individual sellers (blue dots) appear more dispersed geographically, including rural and less commercially dense regions.

Seller Density:

- High concentrations of both individual and company sellers are observed in major urban areas, such as Ho Chi Minh City and Hanoi.
- Coastal areas and cities like Da Nang also exhibit significant activity, reflecting their economic importance.


Thus, the map indicates that companies are more prevalent in commercial hubs, where formal businesses and higher-priced devices dominate, while individual sellers cater to more localized demand.

#### 2.4.2 Listing density by region


In [ ]:
region_counts = (
    df.group_by("region_name")  # Group data by region
    .agg(pl.len().alias("count"))  # Count the number of listings in each region
    .sort("count", descending=True)  # Sort by count in descending order
)

fig = go.Figure(
    go.Bar(
        x=region_counts["region_name"],  # Regions on the x-axis
        y=region_counts["count"],  # Number of listings on the y-axis
        text=region_counts["count"],  # Display the count as text on the bars
        textposition="auto",  # Automatically position the text on the bars
    )
)

fig.update_layout(
    title="Number of Listings by Region",
    xaxis_title="Region",
    yaxis_title="Number of Listings",
    width=fig_width,
    height=fig_height,
    xaxis_tickangle=45,
    **layout,
)
fig.show(config=config)

Throughout Vietnam's 62 Provinces, we can see that:
- Ho Chi Minh City leads with the highest number of listings, far surpassing other regions.
- Following Ho Chi Minh City, regions like Da Nang, Ha Noi, Binh Duong, and Hai Phong also have a significant number of listings. These areas are other urban and economically developed regions.
- Many regions have very low listing counts, with some having just 1–3 listings (e.g., Cao Bang, Ha Giang, Quang Ninh). This indicates limited market activity in rural or remote areas, possibly due to lower demand or lack of sellers.

Overall, the sharp drop-off after the top regions highlights a highly skewed distribution where a few key cities dominate the marketplace.

#### 2.4.3 Price variations across regions


In [ ]:
# Calculate regional price statistics
region_price_stats = (
    df.group_by("region_name")  # Group data by region
    .agg(
        [
            pl.col("price").mean().alias("avg_price"),  # Calculate the average price for each region
            pl.col("price").median().alias("median_price"),  # Calculate the median price
            pl.len().alias("count"),  # Count the number of listings per region
        ]
    )
    .sort("count", descending=True)  # Sort regions by number of listings in descending order
)

# Create box plot
fig = px.box(
    df,
    x="region_name",
    y="price",
    title="Price Distribution by Region",
    labels={"region_name": "Region", "price": "Price (USD)"},
)

fig.update_layout(width=fig_width, height=fig_height, xaxis_tickangle=45, **layout)
fig.show(config=config)

The chart shows the price distribution of smartphones by region, highlighting variations in pricing across different areas.

(1) Price Variability

Wide IQR in major regions:
Regions like Hanoi, Ho Chi Minh City, and other densely populated areas exhibit a wide interquartile range (IQR), indicating diverse pricing. This variability could reflect a mix of high-end and budget products catering to a broad audience.

Narrow IQR in smaller regions:
Smaller or rural regions, such as Kon Tum, Cao Bang, or Ninh Thuan Provinces, show tighter price ranges. These regions may have fewer listings, leading to more consistent pricing patterns.

(2) Median Prices

The median price varies significantly across regions, with urban areas typically having higher medians due to the availability of high-end devices.


(3) Outliers

High price outliers:
Urban centers like Ho Chi Minh City and Hanoi have visible outliers with extremely high prices (exceeding $1,500), likely reflecting luxury or rare items. These outliers can skew average prices but are less representative of typical listings.

Low price uniformity in smaller regions:
The absence of outliers suggests a more homogeneous market with standard or budget-focused listings. That is why regions such as Nam Dinh, Dong Thap, and Soc Trang show more consistent pricing with fewer outliers.

#### 2.4.4 Brand preferences by region


In [ ]:
brand_region = (
    df.group_by(["region_name", "brand"])  # Group data by region and brand
    .agg(pl.len().alias("count"))  # Count the number of listings for each combination
    .sort(["region_name", "count"], descending=[False, True])  # Sort by region and count
)

# Calculate percentage within each region
brand_region = brand_region.with_columns(
    [
        (pl.col("count") / pl.col("count").sum().over("region_name") * 100).alias(
            "percentage"
        )
    ]
)

# Take top 5 brands for each region
brand_region_filtered = brand_region.group_by("region_name").head(5)

fig = px.bar(
    brand_region_filtered.to_pandas(),  # Convert to pandas for compatibility with Plotly Express
    x="region_name",  # Regions on the x-axis
    y="percentage",  # Market share percentage on the y-axis
    color="brand",  # Differentiate segments by brand
    title="Top 5 Brands Market Share by Region",  # Title of the chart
    labels={
        "region_name": "Region",  # Label for the x-axis
        "percentage": "Market Share (%)",  # Label for the y-axis
        "brand": "Brand",  # Label for the legend
    },
)

fig.update_layout(width=fig_width, height=fig_height, xaxis_tickangle=45, **layout)
fig.show(config=config)

The bar chart visualizes the top 5 phone brands by market share in various Vietnam's regions.

- Apple consistently holds the largest market share across nearly all regions, often exceeding 50%. Regions such as Ho Chi Minh City and Hanoi have particularly high shares for Apple, likely due to higher purchasing power and demand for premium devices.

- Samsung is the second most dominant brand, with a significant market share in most regions. Samsung’s share is particularly prominent in regions where Apple’s dominance is less pronounced, highlighting their strong brand recognition and product demand across the country.
- Xiaomi and Oppo are strong contenders in several regions, particularly in mid-tier markets. Their presence reflects their focus on affordability and value for money, catering to budget-conscious consumers.
- Certain regions show higher representation for brands like Vivo and Realme, indicating localized brand preferences or marketing efforts.

(1) Urban areas: In key urban areas, premium brands like Apple and Samsung have a stronger foothold, likely due to higher disposable incomes

(2) Rural regions: In less populated regions, mid-range and budget-friendly brands like Xiaomi, Oppo, and Realme capture a larger share of the market.

In regions with a more fragmented market, the competition among the top 5 brands appears more evenly matched due to: (1) Higher price sensitivity among consumers and (2) Less brand loyalty.

Thus, platforms and sellers can tailor their inventory based on regional market dynamics to maximize sales.

#### 2.4.5 Urban vs rural differences


In [ ]:
# Create an urban/rural classification
# Defining major cities are urban
urban_regions = ["ho_chi_minh_city", "hanoi", "da_nang", "can_tho", "hai_phong"]

df = df.with_columns(
    pl.when(pl.col("region_name").is_in(urban_regions))  # Check if region is urban
    .then(pl.lit("Urban"))  # Classify as "Urban"
    .otherwise(pl.lit("Rural"))  # Otherwise, classify as "Rural"
    .alias("area_type")  # New column name
)

# Price comparison between urban and rural
fig = make_subplots(
    rows=1,  # Single row
    cols=2,  # Two columns
    specs=[[{"type": "box"}, {"type": "pie"}]],  # Box plot in column 1, pie chart in column 2
    subplot_titles=(
        "Price Distribution: Urban vs Rural",  # Title for box plot
        "Listing Distribution: Urban vs Rural",  # Title for pie chart
    ),
)

# Box plot for price distribution
fig.add_trace(
    go.Box(x=df["area_type"], y=df["price"], name="Price Distribution"), row=1, col=1
)

# Pie chart for listing distribution
area_dist = df.group_by("area_type").agg(pl.len().alias("count"))
fig.add_trace(
    go.Pie(
        labels=area_dist["area_type"], # Labels: Urban or Rural
        values=area_dist["count"], # Values: Count of listings
        name="Area Distribution",
    ),
    row=1,
    col=2,
)

fig.update_layout(
    width=fig_width * 1.5,  # Wider for two plots
    height=fig_height,
    **layout,
)
fig.show(config=config)

1. Box Plot - Price Distribution (Urban vs Rural)
- Urban areas: Larger interquartile range (IQR), indicating higher variability in pricing. More high-priced outliers (above the $1,500 range), reflecting hotspots for premium or luxury products.
- Rural areas: Smaller IQR, suggesting more consistent pricing in rural markets. Fewer high-price outliers, indicating a preference for budget or mid-range products.
2. Pie Chart - Listing Distribution.
- Urban listings (79.2%): Urban areas dominate the platform, reflecting higher activity levels due to population density, better infrastructure, and greater digital penetration.
- Rural listings (20.8%): Rural areas contribute a smaller share, possibly due to: Limited access to e-commerce platforms along with fewer sellers and buyers.

Thus,
- The dominance of urban regions in both listing count and price diversity highlights their importance for sellers targeting premium and high-value markets.
- The low representation of rural areas in listings suggests untapped potential, especially as smartphone penetration continues to grow in these regions.

PREMILINARY HYPOTHESES DEVELOPMENT

 1. Price-related Hypotheses:

    *   **Hypothesis 1:** *For each additional GB of storage, the price increases by a statistically significant percentage, and this elasticity differs across brands.*
        *   **Statistical Test:** A linear regression model with interaction to test price elasticity of storage, where storage is measured in GB and interacts with brands.
        *  **Null Hypothesis:** There is no statistically significant change in price with increase in storage capacity, or the elasticity does not differ across brands.
        *   **Observation:** The storage capacity distribution chart shows a clear trend where higher storage (e.g., 256GB, 512GB) correlates with higher prices across brands. This trend is especially strong for premium models (e.g., Apple and Samsung).

    *   **Hypothesis 2:** *The mean price of phones sold by companies is significantly higher than the mean price of phones sold by individuals.*
        *   **Statistical Test:** A two-sample t-test (or a Mann-Whitney U test) to compare the mean prices of company vs. individual sellers.
        *   **Null Hypothesis:** There is no statistically significant difference between the mean price of phones sold by companies and individuals.
        *   **Observation:** While company sellers exhibit less variance and generally consistent higher prices (supported by the boxplot), individual sellers occasionally list rare or premium devices as outliers. On average, companies maintain higher pricing due to new inventory and warranties.

    *   **Hypothesis 3:**  *There is a statistically significant difference in prices among phones with different colors.*
        *   **Statistical Test:** ANOVA test to see if the groups mean are not all the same.
        *   **Null Hypothesis:** The mean price across all colors is the same.
        *   **Observation:** The hypothesis is aligns with consumer behavior. Normal colors (black, white, gold) are expected to have more standardized prices, while niche or rare colors may exhibit price premiums due to exclusivity and limited availability.

2. Seller/Rating-related Hypotheses:

    *   **Hypothesis 4:** *There is a statistically significant positive correlation between seller ratings and phone prices.*
        *   **Statistical Test:** Calculate Pearson correlation coefficient to measure linear correlation (or Spearman rank correlation if data is not normally distributed).
        *   **Null Hypothesis:** There is no statistically significant correlation between seller ratings and phone prices.
        *   **Observation:** The rating distribution chart suggests high ratings dominate, but the connection between pricing and seller ratings has not been explicitly shown. We consider this hypothesis aligns with expectations, but additional data is needed to confirm.

    *   **Hypothesis 5:** *Company sellers have a statistically significant higher average rating than individual sellers.*
        *   **Statistical Test:** Two-sample t-test (or Mann-Whitney U test) to compare mean ratings of company vs. individual sellers.
        *   **Null Hypothesis:** There is no statistically significant difference between the mean ratings of company sellers and individual sellers.
        *   **Observation:** Company sellers are often perceived as more reliable due to warranties and consistent pricing, which could result in higher average ratings. However, this needs specific validation from rating data.

    *   **Hypothesis 6:** *There is a statistically significant positive correlation between the number of `sold_ads` and seller average ratings.*
        *   **Statistical Test:** Pearson correlation coefficient (or Spearman) to measure the relationship.
        *   **Null Hypothesis:** There is no statistically significant correlation between the number of `sold_ads` and seller average ratings.
        *   **Observation:** The hypothesis aligns with the idea that experienced sellers with many sales build trust, resulting in higher ratings. However, we consider more data linking sold_ads and ratings is necessary for confirmation.

3. Geographic-related Hypotheses:

    *   **Hypothesis 7:** *The mean price of phones in major cities (Hanoi, HCMC) is statistically significantly higher than the mean price of phones in other regions.*
        *   **Statistical Test:** ANOVA test to compare multiple group means, followed by post-hoc tests (e.g., Tukey) to find specific differences between regions.
        *   **Null Hypothesis:** There is no statistically significant difference in mean prices among the regions.
        *   **Observation:** The price distribution by region clearly shows that major cities like Ho Chi Minh City and Ha Noi Capital have significantly higher average prices compared to rural areas. This reflects higher purchasing power and demand for premium products.

    *   **Hypothesis 8:** *There is a statistically significant association between brands and regions.*
        *   **Statistical Test:** Chi-squared test to test association of categorical variables.
        *   **Null Hypothesis:** There is no statistically significant association between brand and regions.
        *   **Observation:** While the listing distribution shows geographic concentration, specific brand preferences by region were not provided in the visualizations.

    *   **Hypothesis 9:** *The proportion of high-end phones is significantly higher in urban regions compared to rural regions.*
        *   **Statistical Test:** Chi-squared test to test proportion differences. You need to define a price to denote "high-end".
        *   **Null Hypothesis:** The proportion of high-end phones is not significantly different between urban and rural regions.
        *   **Observation:** The data suggests urban areas like Ho Chi Minh City dominate in listings and high average prices, indicating a higher proportion of premium devices, while rural areas tend to have lower-priced listings, likely reflecting demand for budget-conscious devices.

As a result, price strategies should consider regional affordability, offering discounts or entry-level models in lower-income areas while emphasizing premium features in urban markets.

NEW VARIABLES

Based on all the visualizations and hypotheses, we plan to introduce the following new variables:

**`dominant_colors_by_brand` (Multi-Label Categorical Variable):** Identifies the most frequent colors for each brand, allowing for multiple dominant colors per brand.

- Encoding: Instead of just one dominant color per brand, we will use a multi-label encoding scheme where multiple dominant colors can be assigned. For example, if both black and white are very frequent for Apple, the variable for Apple could be encoded as `[1, 1, 0, ...]` (where each position in the array corresponds to a particular color, black being the first, and white being the second).

- Justification: This approach allows us to capture the fact that multiple colors can be popular within one brand.

**MACHINE LEARNING PLAN:**

**Machine Learning Goal:**

The primary goal is to predict the price of a used phone based on its features, seller attributes, and geographic location. This prediction will provide valuable insights for sellers, buyers, and the platform itself.

**Features Used for Prediction:**

*   **Phone Attributes:** Brand, model, storage capacity, color, condition (new/used).
*   **Seller Attributes:** Seller type (company vs. individual), ratings, sold_ads count.
*   **Geographic Attributes:** Region of sale, urban vs. rural.
*   **Engineered Features:** `dominant_colors_by_brand`.

**Why Predict Prices?**

*   **Market insights for sellers:** To help them competitively price their listings.
*   **Decision-making for buyers:** To help identify fair prices for used phones.
*   **Platform optimization:** To suggest optimal prices to sellers during listing creation.

**Machine Learning Metrics:**

1.  **Mean Absolute Error (MAE):** Measures the average absolute difference between predicted and actual prices (in USD), providing a clear measure of prediction accuracy.
2.  **Root Mean Squared Error (RMSE):** Measures the square root of the average squared difference between predicted and actual prices, giving more weight to larger errors. It's important for capturing outliers and premium phone pricing.
3.  **R-squared (R²):** Measures the proportion of variance in the target variable explained by the model. It is useful to understand model fit.
4.  **Mean Absolute Percentage Error (MAPE):** Measures the prediction error as a percentage of actual values, useful for comparing model performance across different price ranges.

**Machine Learning Models and Methodology:**

1.  **Data Preprocessing:**
    *   **Log Transformation:** Apply a log-transformation to the price variable to reduce the influence of extreme price values.
    *   **Stratified Sampling:** Use stratified sampling to address potential brand-level imbalances.

2.  **Baseline Model:**
    *   **Ridge Regression:** Start with Ridge Regression as the baseline model to balance interpretability and performance. This model will help us to measure the goodness of our engineering features as compared to a simple model.

3.  **Advanced Models:**
    *   **k-Nearest Neighbors (kNN):** Implement kNN to capture non-linear patterns in the data. Use hyperparameter tuning to select the optimal value of 'k'.  We will measure the model performance based on the MAE, RMSE and R².
    *   **Tree-Based Algorithms:** Experiment with tree-based algorithms like Random Forest to capture complex non-linear interactions.

4.  **Feature Importance and Validation:**
    *   **SHAP Analysis:** Use SHAP (SHapley Additive exPlanations) values to analyze and report the importance of features, especially the newly engineered ones. This approach will help us understand how much each feature contributes to prediction.
    *   **Feature Validation:** Validate the significance of engineered variables to assess their usefulness.

5.  **Hyperparameter Tuning and Evaluation:**
    *   **Cross-Validation:** Employ cross-validation techniques (e.g., k-fold) to prevent overfitting and ensure model robustness.
    *  **Grid Search:** Utilize a grid search to tune hyperparameters for each model.

**Potential Challenges:**

*   **Data Imbalance:** There might be an imbalance with brands (e.g., Apple), which may bias the results. Stratified sampling should minimize the effects of imbalanced data.
*   **Outliers:** Extreme prices could affect model performance. Outliers are mitigated by using log transformations, but further analysis might be needed.